<a href="https://colab.research.google.com/github/betty6you/Jing_INFO5731_Spring2020/blob/main/INFO5731_Assignment_Two.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **INFO5731 Assignment Two**

In this assignment, you will try to gather text data from open data source via web scraping or API. After that you need to clean the text data and syntactic analysis of the data.

# **Question 1**



(40 points). Write a python program to collect text data from **either of the following sources** and save the data into a **csv file**:

(1) Collect all the customer reviews of the product [2019 Dell labtop](https://www.amazon.com/Dell-Inspiron-5000-5570-Laptop/dp/B07N49F51N/ref=sr_1_11?crid=1IJ7UWF2F4GHH&keywords=dell%2Bxps%2B15&qid=1580173569&sprefix=dell%2Caps%2C181&sr=8-11&th=1) on amazon.

(2) Collect the top 100 User Reviews of the film [Joker](https://www.imdb.com/title/tt7286456/reviews?ref_=tt_urv) from IMDB.

(3) Collect the abstracts of the top 100 research papers by using the query [natural language processing](https://citeseerx.ist.psu.edu/search?q=natural+language+processing&submit.x=0&submit.y=0&sort=rlv&t=doc) from CiteSeerX.

(4) Collect the top 100 tweets by using hashtag ["#CovidVaccine"](https://twitter.com/hashtag/CovidVaccine) from Twitter. 


In [ ]:
# Write your code here
# I will collect the all the customer reviews of the product 2019 Dell labtop on Amazon
!pip install scrapy
import scrapy


class AmazonReviewsSpider(scrapy.Spider):

  name = "reviews"
  allowed_domains=['amazon.com']
  myBaseUrl="https://www.amazon.com/Dell-Inspiron-5000-5570-Laptop/product-reviews/B07N49F51N/ref=cm_cr_arp_d_paging_btm_next_2?ie=UTF8&reviewerType=all_reviews&pageNumber="
  startURL=[]
  for i in range (1,13):
    startURL.append(myBaseUrl+str(i))
    
  def parse(self, response):
    #Get the Review List
    data = response.css('#cm_cr-review_list')
    
    #Get the Name
    name = data.css('.a-profile-name')
            
    #Get the Review Title
    title = data.css('.review-title')
            
    # Get the Ratings
    star_rating = data.css('.review-rating')
    # Get the users Comments
    comments = data.css('.review-text')
    count = 0
           
    # combining the results
    for review in star_rating:
      yield{
      'Rating': ''.join(review.xpath('.//text()').extract()),
      'Comment': ''.join(comments[count].xpath(".//text()").extract())
         }
      count=count+1

# copy the above code in to the DellSpider.py file
# run file in terminal !scrapy runspider DellSpider.py -o reviews.csv    
      

# **Question 2**

(30 points). Write a python program to **clean the text data** you collected above and save the data in a new column in the csv file. The data cleaning steps include:

(1) Remove noise, such as special characters and punctuations.

(2) Remove numbers.

(3) Remove stopwords by using the [stopwords list](https://gist.github.com/sebleier/554280).

(4) Lowercase all texts

(5) Stemming. 

(6) Lemmatization.

In [ ]:
# Write your code here

!pip install pandas
import pandas as pd
import string
from nltk.corpus import stopwords
import nltk
nltk.download('stopwords')
stop=stopwords.words('english')

data=pd.read_csv(r"https://raw.githubusercontent.com/betty6you/Jing_INFO5731_Spring2020/main/Review.csv")
data['comment'] = data['comment'].apply(lambda x: x.replace(r"'", ''))
data['comment'] = data['comment'].apply(lambda x: x.replace(r'"', ''))
data['comment'] = data['comment'].apply(lambda x: x.replace(r'[\n\n\n\n\n\n\n\n\n\n  \n  \n    , \n  ', ''))
data['comment'] = data['comment'].apply(lambda x: x.replace(r'\n, \n  \n]', ''))

data['stopwords']=data['comment'].apply(lambda x:len ([x for x in x.split( ) if x in stop])) #remove stopwords
data['special_char']=data['comment'].apply(lambda x: len([x for x in x.split() if x.startswith(('**','Â','â€','©','€™'))])) #Remove sepcial characters as noise

data['commnet'] = data['comment'].str.rstrip(string.digits)#remove numbers
data['comment']=data['comment'].str.replace('[^\w\s]','') # punctuation removal

data['comment']=data['comment'].apply(lambda x:" ".join(x.lower() for x in x.split()))# lower casing

from nltk.stem import PorterStemmer
st = PorterStemmer()
data['comment'][:5].apply(lambda x: " ".join([st.stem(word) for word in x.split()])) # Stemming

from textblob import Word
nltk.download('wordnet')
data['comment']= data['comment'].apply(lambda x: " ".join([Word(word).lemmatize() for word in x.split()])) # Lemmatization

data['comment'].to_csv("AmazonReviewupdated.csv",header=True,index=False) # only 1 column with clean sentences

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.


# Question 3

(30 points). Write a python program to conduct **syntax and structure analysis** of the clean text you just saved above. The syntax and structure analysis includes: 

(1) Parts of Speech (POS) Tagging: Tag Parts of Speech of each word in the text, and calculate the total number of N(oun), V(erb), Adj(ective), Adv(erb), respectively.

(2) Constituency Parsing and Dependency Parsing: print out the constituency parsing trees and dependency parsing trees of all the sentences. Using one sentence as an example to explain your understanding about the constituency parsing tree and dependency parsing tree.

(3) Named Entity Recognition: Extract all the entities such as person names, organizations, locations, product names, and date from the clean texts, calculate the count of each entity.

In [ ]:
# Write your code here
import nltk
import spacy
nltk.download('averaged_perceptron_tagger')
from collections import Counter
from spacy import displacy


with open('AmazonReviewupdated.csv') as fp:
  x=fp.readlines()
  for a in x:
    b=a.split()
    tags=nltk.pos_tag(b)# POS Tagging
    counts = Counter( tag for word,  tag in tags)
    print(counts)
    
    
    displacy.render(nlp(a),jupyter=True)#dependency parsing 
    

    nlp = spacy.load("en_core_web_sm")#Name entity recognition
    doc=nlp(a)
    for ent in doc.ents:
      print(ent.text, ent.start_char, ent.end_char, ent.label_)
 

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.
Counter({'NN': 7, 'CC': 3, 'VBG': 3, 'IN': 3, 'VB': 2, 'VBD': 1, 'VBN': 1, 'RB': 1, 'TO': 1, 'VBZ': 1, 'PRP': 1, 'JJ': 1})


Counter({'NN': 23, 'IN': 14, 'JJ': 11, 'DT': 10, 'RB': 7, 'CC': 7, 'VBD': 5, 'VBG': 5, 'PRP': 4, 'VBN': 3, 'VB': 3, 'CD': 2, 'VBP': 2, 'VBZ': 1, 'MD': 1})


evening 8 15 TIME
around 11 16 25 TIME
5 441 442 CARDINAL
Counter({'NN': 14, 'DT': 10, 'IN': 7, 'VBZ': 5, 'RB': 4, 'JJ': 3, 'VBN': 2, 'PRP': 1, 'CC': 1, 'RBR': 1, 'TO': 1, 'VB': 1})


Counter({'NN': 10, 'DT': 8, 'RB': 7, 'VBZ': 4, 'IN': 4, 'JJ': 3, 'VBN': 3, 'CC': 2, 'VBP': 2, 'MD': 1, 'VB': 1, 'PRP': 1, 'NNS': 1, 'VBG': 1, 'CD': 1, 'JJS': 1, 'PRP$': 1})


amazon 174 180 ORG
year 185 189 DATE
one 202 205 CARDINAL
Counter({'JJ': 8, 'NN': 8, 'VBN': 5, 'RB': 4, 'VBD': 3, 'CC': 2, 'VBP': 2, 'DT': 2, 'IN': 2, 'CD': 2, 'PRP': 1, 'RP': 1, 'MD': 1, 'VB': 1, 'WRB': 1})


...

doe 44 47 ORG
Counter({'NN': 2, 'DT': 1, 'PRP$': 1, 'RB': 1})


Counter({'NN': 20, 'DT': 10, 'IN': 8, 'VBD': 8, 'JJ': 7, 'RB': 6, 'CC': 4, 'PRP': 3, 'TO': 2, 'VB': 2, 'VBZ': 2, 'VBP': 2, 'VBG': 1, 'WDT': 1, 'PDT': 1, 'JJR': 1})


a day 122 127 DATE
Counter({'NN': 3, 'PRP': 1, 'VBZ': 1, 'IN': 1, 'DT': 1})


Counter({'JJS': 1, 'NN': 1})


Counter({'NN': 3, 'DT': 3, 'JJ': 2, 'IN': 1, 'PRP': 1, 'VBZ': 1, 'RB': 1, 'CC': 1, 'VBP': 1, 'RBR': 1})


In [ ]:
#constituency parsing 

!pip install benepar
%tensorflow_version 1.x
import benepar
benepar.download('benepar_en3')
import spacy
from benepar.spacy_plugin import BeneparComponent

# Loading spaCy’s en model and adding benepar model to its pipeline
nlp = spacy.load('en')
nlp.add_pipe(BeneparComponent('benepar_en3'))
with open('AmazonReviewupdated.csv') as fp:
  x=fp.readlines()
  #sent = list(doc.sents)[0]
#print(sent._.parse_string)
  for a in x:
    doc=nlp(a)
    print(list(doc.sents)[0]._.parse_string)
# Generating a parse tree for the text

  

[nltk_data] Downloading package benepar_en3 to /root/nltk_data...
[nltk_data]   Package benepar_en3 is already up-to-date!
(S (NP (NP (NP (NN product)) (VP (VBD arrived) (ADJP (VBN damaged)))) (CC and) (NP (ADJP (RB not) (VBG working)) (NN seller))) (VP (VBP refuse) (S (VP (TO to) (VP (VB fix) (CC or) (VB replace))))) (CC and) (VP (VP (VBZ is) (VP (VBG blaming) (NP (PRP me)) (PP (IN for) (NP (NN damage))) (ADJP (JJ beware) (PP (IN of) (S (VP (VBG purchasing) (PP (IN from) (NP (NML (JJ brown) (NN box)) (NN seller))))))))) (_SP 
)))
(S (VP (S (VP (VBD came) (PP (IN in) (NP (NN evening))) (PP (IN around) (NP (CD 11) (RB pm))))) (RB so) (S (IN in) (NP (JJ thankful) (NNS usps) (FW wa)) (VP (ADVP (RB still)) (VBG working)) (CC but) (VP (VBD had) (NP (NP (DT a) (JJ few) (NN scratch)) (PP (IN on) (NP (DT the) (NN outside)))) (SBAR (IN a) (IN if) (S (NP (PRP it)) (ADVP (RB ha)) (VP (VBN been) (VP (VBN used)))))))))
(NP (DT this) (NN laptop))
(S (NP (DT this)) (VP (VBZ is) (RB not) (NP (DT the) 

**Write your explanations of the constituency parsing tree and dependency parsing tree here (Question 3-2):** 

In [ ]:
'''
Write your explanations of the constituency parsing tree and dependency parsing tree here

A constituency parse tree breaks a text into sub-phrases. Non-terminals in the tree are types of phrases, the terminals are the words in the sentence, and the edges are unlabeled. 
A dependency parse connects words according to their relationships. Each vertex in the tree represents a word, child nodes are words that are dependent on the parent, and edges are labeled by the relationship. 
'''

'\nWrite your explanations of the constituency parsing tree and dependency parsing tree here\n\n\n\n'